In [28]:
import pymongo
import pandas as pd
import numpy as np

client = pymongo.MongoClient("localhost", 27017)

db = client['season2020']
test = db.games.find()

In [13]:
player = 'LeBron James'
stat = 'PTS'
cursor = db.games.find({"teamA_stats."+player:{"$exists":True}},{"teamA_stats."+player+"."+stat:1,"_id":False})
# value = [doc['teamA_stats'][player][stat] for doc in cursor]
# cursor1 = db.games.find({"teamH_stats."+player:{"$exists":True}},{"teamH_stats."+player+"."+stat:1,"_id":False})
# value1 = [doc['teamH_stats'][player][stat] for doc in cursor1]
# values = value + value1
# num_values = [float(num) for num in values if (num is not None) and (num is not '')]
# stat_mean = np.array(num_values).mean().round(2)

In [14]:
pd.DataFrame(cursor)

teamA_stats
0   {'LeBron James': {'PTS': '18'}}
1   {'LeBron James': {'PTS': '39'}}
2   {'LeBron James': {'PTS': '21'}}
3   {'LeBron James': {'PTS': '30'}}
4   {'LeBron James': {'PTS': '19'}}
5   {'LeBron James': {'PTS': '23'}}
6   {'LeBron James': {'PTS': '30'}}
7   {'LeBron James': {'PTS': '33'}}
8   {'LeBron James': {'PTS': '29'}}
9   {'LeBron James': {'PTS': '25'}}
10  {'LeBron James': {'PTS': '20'}}
11  {'LeBron James': {'PTS': '31'}}
12  {'LeBron James': {'PTS': '25'}}
13  {'LeBron James': {'PTS': '28'}}
14  {'LeBron James': {'PTS': '32'}}

In [29]:
team = 'LAL'
cursor3 = db.games.find({})
list_games = [i for i in cursor3]

In [16]:
cursor3 = db.games.find({},{"game_score":1, "_id":False})

In [26]:
list_games = [i for i in cursor3]

In [30]:
list_games

[{'_id': ObjectId('5df1857568dce531ba175a3c'),
  'game_id': '201910220TOR',
  'game_date': '20191022',
  'teamA': 'NOP',
  'teamH': 'TOR',
  'game_score': {'NOP': {'1': '30',
    '2': '31',
    '3': '25',
    '4': '31',
    'OT': '5',
    'T': '122'},
   'TOR': {'1': '27',
    '2': '29',
    '3': '32',
    '4': '29',
    'OT': '13',
    'T': '130'}},
  'teamA_stats': {'Jrue Holiday': {'MP': '41:05',
    'FG': '6',
    'FGA': '15',
    'FG%': '.400',
    '3P': '1',
    '3PA': '6',
    '3P%': '.167',
    'FT': '0',
    'FTA': '2',
    'FT%': '.000',
    'ORB': '2',
    'DRB': '2',
    'TRB': '4',
    'AST': '6',
    'STL': '0',
    'BLK': '2',
    'TOV': '5',
    'PF': '2',
    'PTS': '13',
    '+/-': '-14'},
   'Brandon Ingram': {'MP': '35:06',
    'FG': '8',
    'FGA': '19',
    'FG%': '.421',
    '3P': '2',
    '3PA': '5',
    '3P%': '.400',
    'FT': '4',
    'FTA': '4',
    'FT%': '1.000',
    'ORB': '0',
    'DRB': '5',
    'TRB': '5',
    'AST': '5',
    'STL': '1',
    'BLK': '2'

In [19]:
keys = list_games[0]['game_score'].keys()

In [20]:
for team in keys:
    print(list_games[0]['game_score'][team]['T'])

122
130


In [21]:
len(list_games)

400

In [22]:
team =  list_games[0]['teamA']
team

KeyError: 'teamA'

In [ ]:
game_id = list_games[0]['game_id']
date = list_games[0]['game_date']
team_a =  list_games[0]['teamA']
team_b =  list_games[0]['teamH']

df_a = pd.DataFrame.from_dict(list_games[0]['teamA_stats'], orient='index')
df_a.dropna(inplace=True)
df_b = pd.DataFrame.from_dict(list_games[0]['teamH_stats'], orient='index')
df_b.dropna(inplace=True)
df_a['Away'] = 1
df_b['Away'] = 0

col_stats = ['FG','FGA','3P','3PA', 'FT', 'FTA',
             'TRB','ORB','DRB', 'AST', 'STL', 'BLK', 'TOV', 'PF', 'PTS']

df_a = pd.DataFrame(df_a[col_stats].astype('int32').sum())
df_a.columns = [team_a]
# df_a['Away'] = 1
df_b = pd.DataFrame(df_b[col_stats].astype('int32').sum())
df_b.columns = [team_b]
# df_b['Away'] = 0

totals = pd.concat([df_a, df_b], axis=1, sort=False)
totals = totals.transpose()


In [31]:
store_df = pd.DataFrame()
for match in list_games:
    
    game_id = match['game_id']
    date = match['game_date']
    team_a =  match['teamA']
    team_b =  match['teamH']

    df_a = pd.DataFrame.from_dict(match['teamA_stats'], orient='index')
    df_a.dropna(inplace=True)
    df_b = pd.DataFrame.from_dict(match['teamH_stats'], orient='index')
    df_b.dropna(inplace=True)
    df_a['Away'] = 1
    df_b['Away'] = 0

    col_stats = ['Away','FG','FGA','3P','3PA', 'FT', 'FTA',
                 'TRB','ORB','DRB', 'AST', 'STL', 'BLK', 'TOV', 'PF', 'PTS']

    df_a = pd.DataFrame(df_a[col_stats].astype('float').sum())
    df_a.columns = [team_a]
    df_b = pd.DataFrame(df_b[col_stats].astype('float').sum())
    df_b.columns = [team_b]
    df_a.loc['Opp',:]=team_b
    df_b.loc['Opp',:]=team_a

    totals = pd.concat([df_a, df_b], axis=1, sort=False)
    totals = totals.transpose()

    store_df = pd.concat([store_df,totals])

In [32]:
store_df

Away  FG  FGA  3P 3PA  FT FTA TRB ORB DRB AST STL BLK TOV  PF  PTS  Opp
NOP   12  43  102  19  45  17  20  53  16  37  30   4   9  19  34  122  TOR
TOR    0  42  103  14  40  32  38  57  16  41  23   7   3  16  24  130  NOP
LAL   10  37   85  13  33  15  21  41   9  32  20   4   7  14  24  102  LAC
LAC    0  42   81  11  31  17  24  45  11  34  24   8   5  14  25  112  LAL
CHI   10  49  105   9  30  18  22  49  20  29  25  11   4  10  20  125  CHO
..   ...  ..  ...  ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ...  ...
MIL    0  44  105  11  41  17  24  52  15  37  29   8   4   8  23  116  DAL
CHI   10  43   87   9  31  11  13  31   5  26  27  17   6  13  21  106  OKC
OKC    0  35   69  16  34  23  28  42   9  33  21   8   6  26  15  109  CHI
POR   10  40   84  14  34  17  20  41   9  32  21   9   9  20  27  111  PHO
PHO    0  41   90  12  34  16  19  44  11  33  31  11   5  20  21  110  POR

[800 rows x 17 columns]

In [ ]:
col = col_stats + ['Opp']
col

In [ ]:
store_np = np.array(store_df)

In [ ]:
store_np

In [322]:
mean_df = pd.DataFrame()
team_list = ['NOP', 'LAL', 'BOS','DAL','GSW']
stats = ['PTS','TRB','BLK']
for team in team_list:
    mean_df.loc[team,'Avg_PTS'] = store_df.loc[team,'PTS'].sum()/store_df.loc[team,'PTS'].count()
    mean_df.loc[team,'Avg_TRB'] = store_df.loc[team,'TRB'].sum()/store_df.loc[team,'TRB'].count()
    mean_df.loc[team,'Avg_AST'] = store_df.loc[team,'AST'].sum()/store_df.loc[team,'AST'].count()
    mean_df.loc[team,'Avg_BLK'] = store_df.loc[team,'BLK'].sum()/store_df.loc[team,'BLK'].count()
    mean_df.loc[team,'Avg_STL'] = store_df.loc[team,'STL'].sum()/store_df.loc[team,'STL'].count()
    mean_df.loc[team,'Avg_TOV'] = store_df.loc[team,'TOV'].sum()/store_df.loc[team,'TOV'].count()

Away  FG  FGA  3P 3PA  FT FTA TRB ORB DRB AST STL BLK TOV  PF  PTS  Opp
NOP   12  43  102  19  45  17  20  53  16  37  30   4   9  19  34  122  TOR
TOR    0  42  103  14  40  32  38  57  16  41  23   7   3  16  24  130  NOP
LAL   10  37   85  13  33  15  21  41   9  32  20   4   7  14  24  102  LAC
LAC    0  42   81  11  31  17  24  45  11  34  24   8   5  14  25  112  LAL
CHI   10  49  105   9  30  18  22  49  20  29  25  11   4  10  20  125  CHO
..   ...  ..  ...  ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ...  ...
MIL    0  44  105  11  41  17  24  52  15  37  29   8   4   8  23  116  DAL
CHI   10  43   87   9  31  11  13  31   5  26  27  17   6  13  21  106  OKC
OKC    0  35   69  16  34  23  28  42   9  33  21   8   6  26  15  109  CHI
POR   10  40   84  14  34  17  20  41   9  32  21   9   9  20  27  111  PHO
PHO    0  41   90  12  34  16  19  44  11  33  31  11   5  20  21  110  POR

[800 rows x 17 columns]

In [42]:
store_df.loc['LAL',:]

Away  FG  FGA  3P 3PA  FT FTA TRB ORB DRB AST STL BLK TOV  PF  PTS
Opp                                                                   
LAL    0  42   81  11  31  17  24  45  11  34  24   8   5  14  25  112
LAL   13  29   70   8  25  20  21  40   3  37  19   8   2  22  25   86
LAL   12  35   91  10  35  21  23  45  13  32  19   7   4  14  20  101
LAL   13  31   95   7  34  22  23  46  13  33  20  10   3  21  27   91
LAL    0  40  102  14  36  16  23  61  18  43  23   5   1  22  21  110
LAL    0  33   83   6  25  24  29  47   8  39  23  11   4  17  18   96
LAL    0  43   85  14  32  12  23  42   7  35  22  11   4  16  21  112
LAL   10  28   80   6  35  18  24  37   8  29  18   9   2  12  12   80
LAL   10  43   89  12  36  15  22  43   7  36  26   6   8  13  17  113
LAL    0  43   91  16  38  13  17  39   6  33  32   3   4  11  22  115
LAL   10  36   89   9  35  13  17  33  10  23  29   8   7  17  14   94
LAL   11  36   82  16  39   9   9  43  10  33  24   7   0  17  22   97
LAL   13  37   86   8  28  19  25  37   9  28  16  11   2  18  19  101
LAL   10  38   80   9  28  22  25  39   8  31  22  10   2  15  22  107
LAL    0  49   93  11  31  18  20  37   6  31  28   8   3  11  23  127
LAL    0  43   89  14  30   8  13  47  12  35  28  12   3  19  19  108
LAL    0  41   88  10  25  12  15  41   9  32  23   4   5  13  22  104
LAL    0  34   84  17  40  25  30  42  13  29  20   7   4  19  23  110
LAL   11  38   96  10  37  17  19  45  13  32  25  10   2  17  23  103
LAL   11  42   97  17  49  13  18  51  16  35  24  11   1  13  20  114
LAL    0  37   91   6  29  16  17  35   7  28  26   9   4  11  25   96
LAL    0  34   83  14  31  14  19  40   8  32  20   3   3  18  24   96
LAL    0  39   86  10  34  25  29  34   4  30  20   9   4  15  25  113
LAL   13  44   85  15  37  22  26  33   7  26  27   5   6  15  18  125
LAL    0  34   81   8  26  11  17  41   8  33  20  10   5  14  17   87
LAL    0  39   85  10  33  22  28  34   5  29  24   8   2   8  21  110
LAL    0  31   86  12  42  22  25  42   8  34  18   8   5  19  27   96

In [33]:
mean_df = pd.DataFrame()
team_list = ['NOP', 'LAL', 'BOS','DAL','GSW']
stats = col_stats
for team in team_list:
    for stat in stats:
        label = 'Avg_'+ stat 
        mean_df.loc[team,label] = store_df.loc[team,stat].sum()/store_df.loc[team,stat].count()

In [34]:
mean_df

Avg_Away     Avg_FG    Avg_FGA     Avg_3P    Avg_3PA     Avg_FT  \
NOP  5.111111  41.333333  91.555556  14.185185  38.777778  15.962963   
LAL  5.851852  42.814815  88.222222  10.962963  30.370370  16.666667   
BOS  6.333333  40.458333  89.333333  12.375000  34.583333  17.541667   
DAL  4.769231  42.000000  90.038462  14.846154  40.807692  19.346154   
GSW  5.464286  38.035714  88.321429   9.178571  28.392857  19.071429   

       Avg_FTA    Avg_TRB    Avg_ORB    Avg_DRB    Avg_AST   Avg_STL  \
NOP  21.777778  44.111111  10.370370  33.740741  25.037037  7.666667   
LAL  22.703704  45.925926  10.074074  35.851852  26.185185  8.851852   
BOS  21.958333  45.166667  10.291667  34.875000  23.458333  8.291667   
DAL  24.961538  48.076923  10.653846  37.423077  24.692308  6.230769   
GSW  23.428571  42.928571  10.392857  32.535714  23.714286  8.321429   

      Avg_BLK    Avg_TOV     Avg_PF     Avg_PTS  
NOP  4.814815  15.592593  23.000000  112.814815  
LAL  7.148148  14.777778  20.111111  113.259259  
BOS  5.916667  12.583333  21.666667  110.833333  
DAL  4.423077  12.192308  19.538462  118.192308  
GSW  4.642857  14.214286  19.464286  104.321429

In [23]:
list_games

[{'game_score': {'NOP': {'1': '30',
    '2': '31',
    '3': '25',
    '4': '31',
    'OT': '5',
    'T': '122'},
   'TOR': {'1': '27',
    '2': '29',
    '3': '32',
    '4': '29',
    'OT': '13',
    'T': '130'}}},
 {'game_score': {'LAL': {'1': '25',
    '2': '29',
    '3': '31',
    '4': '17',
    'T': '102'},
   'LAC': {'1': '22', '2': '40', '3': '23', '4': '27', 'T': '112'}}},
 {'game_score': {'CHI': {'1': '28',
    '2': '27',
    '3': '40',
    '4': '30',
    'T': '125'},
   'CHO': {'1': '37', '2': '26', '3': '33', '4': '30', 'T': '126'}}},
 {'game_score': {'DET': {'1': '27',
    '2': '27',
    '3': '29',
    '4': '36',
    'T': '119'},
   'IND': {'1': '24', '2': '31', '3': '31', '4': '24', 'T': '110'}}},
 {'game_score': {'CLE': {'1': '24',
    '2': '17',
    '3': '24',
    '4': '20',
    'T': '85'},
   'ORL': {'1': '28', '2': '27', '3': '16', '4': '23', 'T': '94'}}},
 {'game_score': {'MIN': {'1': '33',
    '2': '35',
    '3': '20',
    '4': '27',
    'OT': '12',
    'T': '127'},
 

In [188]:
totals = pd.DataFrame(df.sum())
totals.columns = [team]

In [242]:
store_df

Away  FG  FGA  3P  3PA  FT  FTA  TRB  ORB  DRB  AST  STL  BLK  TOV  PF  \
NOP    12  43  102  19   45  17   20   53   16   37   30    4    9   19  34   
TOR     0  42  103  14   40  32   38   57   16   41   23    7    3   16  24   
LAL    10  37   85  13   33  15   21   41    9   32   20    4    7   14  24   
LAC     0  42   81  11   31  17   24   45   11   34   24    8    5   14  25   
CHI    10  49  105   9   30  18   22   49   20   29   25   11    4   10  20   
..    ...  ..  ...  ..  ...  ..  ...  ...  ...  ...  ...  ...  ...  ...  ..   
MIL     0  44  105  11   41  17   24   52   15   37   29    8    4    8  23   
CHI    10  43   87   9   31  11   13   31    5   26   27   17    6   13  21   
OKC     0  35   69  16   34  23   28   42    9   33   21    8    6   26  15   
POR    10  40   84  14   34  17   20   41    9   32   21    9    9   20  27   
PHO     0  41   90  12   34  16   19   44   11   33   31   11    5   20  21   

     PTS  
NOP  122  
TOR  130  
LAL  102  
LAC  112  
CHI  125  
..   ...  
MIL  116  
CHI  106  
OKC  109  
POR  111  
PHO  110  

[800 rows x 16 columns]

In [192]:
df_a

MP FG FGA    FG% 3P 3PA   3P% FT FTA    FT% ORB  \
Jrue Holiday              41:05  6  15   .400  1   6  .167  0   2   .000   2   
Brandon Ingram            35:06  8  19   .421  2   5  .400  4   4  1.000   0   
JJ Redick                 27:03  6   9   .667  4   6  .667  0   0          0   
Lonzo Ball                24:50  2   7   .286  2   3  .667  2   2  1.000   0   
Derrick Favors            20:46  3   6   .500  0   0        0   0          1   
Josh Hart                 28:10  4   9   .444  3   5  .600  4   4  1.000   4   
Nicolò Melli              19:37  5   7   .714  4   5  .800  0   0          2   
Kenrich Williams          18:02  0   4   .000  0   2  .000  3   3  1.000   3   
Frank Jackson             13:51  3   6   .500  1   3  .333  2   2  1.000   0   
Jahlil Okafor             12:29  3   3  1.000  0   0        2   3   .667   2   
E'Twaun Moore             12:06  2   7   .286  1   3  .333  0   0          1   
Nickeil Alexander-Walker  11:55  1  10   .100  1   7  .143  0   0          1   

                         DRB TRB AST STL BLK TOV PF PTS  +/-  
Jrue Holiday               2   4   6   0   2   5  2  13  -14  
Brandon Ingram             5   5   5   1   2   2  4  22  -19  
JJ Redick                  2   2   1   0   0   3  3  16  -14  
Lonzo Ball                 5   5   5   0   0   1  2   8   -7  
Derrick Favors             6   7   2   0   1   1  5   6  -12  
Josh Hart                  6  10   1   0   1   1  4  15   -1  
Nicolò Melli               3   5   2   0   0   2  1  14  +11  
Kenrich Williams           3   6   3   1   2   1  5   3  +11  
Frank Jackson              0   0   1   0   0   1  3   9   +7  
Jahlil Okafor              0   2   0   0   1   1  3   8   -7  
E'Twaun Moore              2   3   2   0   0   0  0   5   -1  
Nickeil Alexander-Walker   3   4   2   2   0   1  2   3   +6

In [167]:
totals.set_index('NOP')

Empty DataFrame
Columns: []
Index: [43, 102, 19, 45, 17, 20, 53, 16, 37, 30, 4, 9, 19, 34, 122]

In [165]:
game_id = list_games[0]['game_id']
team_a =  list_games[0]['teamA']
team_b =  list_games[0]['teamH']

df_a = list_games[0]['teamA_stats']
df_b = list_games[0]['teamH_stats']

df_game = pd.DataFrame({'game':game_id, 'team_a':team_a, 'team_b':team_b, 'stats_a': df_a, 'stats_b':df_b})

# df_b.dropna(inplace=True)
# df = df[['FG','FGA','3P','3PA', 'FT', 'FTA', 'TRB','ORB','DRB', 'AST', 'STL', 'BLK', 'TOV', 'PF', 'PTS']].astype('int32')

In [157]:
pd.DataFrame(df.sum())

RangeIndex(start=0, stop=1, step=1)

In [145]:
a.sum()

PTS    122
dtype: int64